# Data Analysis

## Imports

In [126]:
import os
import warnings

import pandas as pd
import plotly.express as px
from dotenv import load_dotenv

from app.src.Database import Database

warnings.simplefilter("ignore")

load_dotenv("app/.env")

True

In [24]:
database = Database(
    user=os.getenv("DB_USER"),
    password=os.getenv("DB_PASSWORD"),
    host=os.getenv("DB_HOST"),
    port=os.getenv("DB_PORT"),
    database=os.getenv("DB_NAME"),
)

INFO: Database is accessible


## Database Schema

In [25]:
# display all tables
query = (
    "SELECT table_name "
    "FROM information_schema.tables "
    "WHERE table_schema = 'open_discourse' "
    "ORDER BY table_name;"
)
print(database.fetch_data(query))
print()
for table in database.fetch_data(query)["table_name"]:
    table_schema = f"SELECT column_name FROM information_schema.columns WHERE table_name = '{table}';"
    print(table)
    print(database.fetch_data(table_schema)["column_name"].tolist())
    print()

                 table_name
0    contributions_extended
1  contributions_simplified
2           electoral_terms
3                  factions
4               politicians
5                  speeches

contributions_extended
['faction_id', 'politician_id', 'speech_id', 'text_position', 'id', 'type', 'first_name', 'last_name', 'content']

contributions_simplified
['id', 'text_position', 'speech_id', 'content']

electoral_terms
['id', 'start_date', 'end_date']

factions
['id', 'abbreviation', 'full_name']

politicians
['id', 'birth_date', 'death_date', 'birth_place', 'birth_country', 'aristocracy', 'academic_title', 'gender', 'profession', 'first_name', 'last_name']

speeches
['id', 'session', 'electoral_term', 'politician_id', 'faction_id', 'date', 'search_speech_content', 'position_long', 'document_url', 'first_name', 'last_name', 'position_short', 'speech_content']



## Data Analysis

In [26]:
# get all tables content in the database
speeches = database.fetch_data("SELECT * FROM open_discourse.speeches;")
contributions = database.fetch_data(
    "SELECT * FROM open_discourse.contributions_extended;"
)
politicians = database.fetch_data("SELECT * FROM open_discourse.politicians;")
electoral_terms = database.fetch_data("SELECT * FROM open_discourse.electoral_terms;")
factions = database.fetch_data("SELECT * FROM open_discourse.factions;")

### Visualizations

In [27]:
# define global plotly styling
px.defaults.template = "plotly_white"
px.defaults.width = 900
px.defaults.height = 600
px.defaults.color_discrete_sequence = px.colors.qualitative.Safe

In [97]:
# histogram that shows distribution of speeches among electoral terms
count = (
    speeches.groupby("electoral_term")["id"].count().reset_index(name="num_speeches")
)

fig = px.bar(
    count,
    x="electoral_term",
    y="num_speeches",
    title="Verteilung der Anzahl an Reden nach Wahlperioden",
)

fig.add_hline(
    y=count["num_speeches"].mean(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Durchschnitt: {count['num_speeches'].mean():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="white",
)

fig.add_hline(
    y=count["num_speeches"].max(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Max: {count['num_speeches'].max():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="white",
)

fig.add_hline(
    y=count["num_speeches"].min(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Min: {count['num_speeches'].min():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="rgba(255, 255, 255, 0.8)",
)

# Set bar color to a darker blue
fig.update_traces(marker_color="#384860")

fig.update_layout(
    font=dict(family="Helvetica, Arial, sans-serif", size=16),
    title=dict(font=dict(size=20), x=0.5, xanchor="center"),
    xaxis_title="Wahlperiode",
    yaxis_title="Anzahl Reden",
    bargap=0.2,
    margin=dict(l=80, r=20, t=80, b=80),
)

fig.update_xaxes(
    tickangle=45,
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
)
fig.update_yaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
    gridcolor="rgba(0,0,0,0.1)",
)

fig.show()

In [103]:
# histogram that shows the distribution of speeches in the electoral term 20

count_20 = (
    speeches.loc[speeches["electoral_term"] == 20]
    .groupby("session")["id"]
    .count()
    .reset_index(name="num_speeches")
)

fig = px.bar(
    count_20,
    x="session",
    y="num_speeches",
    title="Verteilung der Anzahl an Reden in der Wahlperiode 20",
    labels={"session": "Session", "num_speeches": "Anzahl der Reden"},
)

fig.add_hline(
    y=count_20["num_speeches"].mean(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Durchschnitt: {count_20['num_speeches'].mean():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="white",
)

fig.add_hline(
    y=count_20["num_speeches"].max(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Max: {count_20['num_speeches'].max():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="white",
)

fig.add_hline(
    y=count_20["num_speeches"].min(),
    line_dash="dash",
    line_color="red",
    annotation_text=f"Min: {count_20['num_speeches'].min():.0f}",
    annotation_position="top left",
    annotation_font=dict(color="red", size=14),
    annotation_bgcolor="rgba(255, 255, 255, 0.9)",
)

fig.update_traces(marker_color="#384860")

fig.update_layout(
    font=dict(family="Helvetica, Arial, sans-serif", size=16),
    title=dict(font=dict(size=20), x=0.5, xanchor="center"),
    xaxis_title="Session",
    yaxis_title="Anzahl",
    bargap=0.2,
    margin=dict(l=80, r=20, t=80, b=80),
)

fig.update_xaxes(
    tickangle=45,
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
)
fig.update_yaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
    gridcolor="rgba(0,0,0,0.1)",
    # type="log",
)

fig.show()

In [102]:
speech_ids_20 = speeches.loc[speeches["electoral_term"] == 20, "id"]
contributions_20 = contributions.loc[contributions["speech_id"].isin(speech_ids_20)]
contributions_20

id     type first_name last_name  politician_id content  \
2519308  2519308  Beifall                                  -1           
2519309  2519309  Beifall                                  -1           
2519310  2519310  Beifall                                  -1           
2519311  2519311  Beifall                                  -1           
2519312  2519312  Beifall                                  -1           
...          ...      ...        ...       ...            ...     ...   
2912063  2912063  Beifall                                  -1           
2912064  2912064  Beifall                                  -1           
2912065  2912065  Beifall     Robert     Farle       11005053           
2912066  2912066  Beifall                                  -1           
2912067  2912067  Beifall                                  -1           

         speech_id  text_position  faction_id  
2519308    1067311              0          25  
2519309    1067311              0          15  
2519310    1067311              0           4  
2519311    1067312              0           5  
2519312    1067313              0           5  
...            ...            ...         ...  
2912063    1124594              1           0  
2912064    1124594              1          15  
2912065    1124594              2          18  
2912066    1124594              2           0  
2912067    1124594              2          15  

[392760 rows x 9 columns]

In [108]:
# histogramm that shows the distribution of contribution types

# Order categories by frequency (descending)
order = (
    contributions_20["type"].value_counts().sort_values(ascending=False).index.tolist()
)

fig = px.histogram(
    contributions_20,
    x="type",
    title="Verteilung der Interventionsarten nach Häufigkeit in der Wahlperiode 20",
    category_orders={"type": order},
)

# Set bar color to a darker blue
fig.update_traces(marker_color="#384860")

fig.update_layout(
    font=dict(family="Helvetica, Arial, sans-serif", size=16),
    title=dict(font=dict(size=20), x=0.5, xanchor="center"),
    xaxis_title="Interventions-Typ",
    yaxis_title="Anzahl",
    bargap=0.2,
    margin=dict(l=80, r=20, t=80, b=80),
)

fig.update_xaxes(
    tickangle=45,
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
)
fig.update_yaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
    mirror=True,
    gridcolor="rgba(0,0,0,0.1)",
    type="log",
)

fig.show()

In [137]:
# plot length distribution of speeches in electoral_term 20

speeches_20["text_length"] = speeches_20["speech_content"].str.split().str.len()

fig = px.histogram(
    speeches_20,
    x="text_length",
    nbins=50,
    title="Verteilung der Länge der Reden in der Wahlperiode 20",
)

# Set bar color to a darker blue
fig.update_traces(marker_color="#384860")

fig.update_layout(
    font=dict(family="Helvetica, Arial, sans-serif", size=16),
    title=dict(font=dict(size=20), x=0.5, xanchor="center"),
    xaxis_title="Länge der Reden (Wörter)",
    yaxis_title="Anzahl",
    bargap=0.3,
    margin=dict(l=80, r=20, t=80, b=80),
)

fig.update_xaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
)
fig.update_yaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
    gridcolor="rgba(0,0,0,0.1)",
    type="log",
)

fig.show()

In [ ]:
import numpy as np
import plotly.express as px

# add word count to data
speeches_20["text_length"] = speeches_20["speech_content"].str.split().str.len()


BIN = 100
xmin = int(np.nanmin(speeches_20["text_length"]))
xmax = int(np.nanmax(speeches_20["text_length"]))


start = (xmin // BIN) * BIN
end = int(np.ceil((xmax + 1) / BIN) * BIN)

# build edges/centers
edges = np.arange(start, end, BIN)
centers = edges + BIN / 2
labels = [f"{left}–{left + BIN - 1}" for left in edges]

# choose a labeling step
step = max(1, len(labels) // 12)

fig = px.histogram(
    speeches_20,
    x="text_length",
    nbins=None,
    title="Verteilung der Länge der Reden in der Wahlperiode 20",
)

# apply the bins so bars match our labels
fig.update_traces(
    xbins=dict(start=start, end=end, size=BIN),
    marker_color="#384860",
)

fig.update_layout(
    font=dict(family="Helvetica, Arial, sans-serif", size=16),
    title=dict(font=dict(size=20), x=0.5, xanchor="center"),
    xaxis_title=f"Länge der Rede (Wörter)",
    yaxis_title="Anzahl",
    bargap=0.1,
    margin=dict(l=80, r=20, t=80, b=80),
)

fig.update_xaxes(
    tickmode="array",
    tickvals=centers[::step],
    ticktext=labels[::step],
    tickangle=45,
    ticks="outside",
    ticklen=6,
    showline=True,
    linewidth=1,
    linecolor="black",
    gridcolor="rgba(0,0,0,0.08)",
)

fig.update_yaxes(
    showline=True,
    linewidth=1,
    linecolor="black",
    gridcolor="rgba(0,0,0,0.1)",
    type="log",
)

fig.show()